1. Setup Mario

In [11]:
%pip install gym_super_mario_bros==7.4.0 nes_py==8.2.1

Note: you may need to restart the kernel to use updated packages.


You should consider upgrading via the 'c:\Users\Gebruiker\AppData\Local\Programs\Python\Python38\python.exe -m pip install --upgrade pip' command.


In [14]:
import numpy
print(numpy.__version__)


1.24.4


In [1]:
# Import the game
import gym_super_mario_bros
# Import the Joypad wrapper
from nes_py.wrappers import JoypadSpace
# Import the SIMPLIFIED controls
from gym_super_mario_bros.actions import SIMPLE_MOVEMENT

In [2]:
# Setup game
env = gym_super_mario_bros.make('SuperMarioBros-v0',apply_api_compatibility=True,render_mode="human" )
env = JoypadSpace(env, SIMPLE_MOVEMENT)

c:\Users\Gebruiker\AppData\Local\Programs\Python\Python38\lib\site-packages\gym\envs\registration.py:555: UserWarning: WARN: The environment SuperMarioBros-v0 is out of date. You should consider upgrading to version `v3`.
  logger.warn(
c:\Users\Gebruiker\AppData\Local\Programs\Python\Python38\lib\site-packages\gym\envs\registration.py:627: UserWarning: WARN: The environment creator metadata doesn't include `render_modes`, contains: ['render.modes', 'video.frames_per_second']
  logger.warn(


In [ ]:
# Create a flag - restart or not
done = True
# Loop through each frame in the game - step = frame
for step in range(100000):
    # Start the game to begin with
    if done:
        # Start the game
        env.reset()
    # Do random action
    # env.step() allows us to take a step
    # env.action_sapce.sample() allows us to take a random action
    state, reward, terminated, truncated, info = env.step(env.action_space.sample())
    done = terminated or truncated
    # Show the game on the screen
    env.render()
# Close the game
env.close()

In [49]:
# If need to close game early
env.close()

ValueError: env has already been closed.

: 

In [36]:
state = env.reset()

2. Preprocess Enviroment

In [3]:
# IMport Frame Stacker Wrapper and GrayScaling Wrapper
from gym.wrappers import GrayScaleObservation
# Import Vectorization Wrappers
from stable_baselines3.common.vec_env import VecFrameStack, DummyVecEnv
# Import Matplotlib to show the impact of frame stacking
from matplotlib import pyplot as plt

This is the environment

In [4]:
# 1. Create the base environment
env = gym_super_mario_bros.make('SuperMarioBros-v0',apply_api_compatibility=True,render_mode="human" )
# 2. Simplify the controls
env = JoypadSpace(env, SIMPLE_MOVEMENT)
# 3. Grayscale
env = GrayScaleObservation(env, keep_dim=True)
# 4. Wrap inside the Dummy Environement
env = DummyVecEnv([lambda: env])
# 5. Stack the frames
env = VecFrameStack(env, 4, channels_order='last')

c:\Users\Gebruiker\AppData\Local\Programs\Python\Python38\lib\site-packages\gym\envs\registration.py:555: UserWarning: WARN: The environment SuperMarioBros-v0 is out of date. You should consider upgrading to version `v3`.
  logger.warn(
c:\Users\Gebruiker\AppData\Local\Programs\Python\Python38\lib\site-packages\gym\envs\registration.py:627: UserWarning: WARN: The environment creator metadata doesn't include `render_modes`, contains: ['render.modes', 'video.frames_per_second']
  logger.warn(
c:\Users\Gebruiker\AppData\Local\Programs\Python\Python38\lib\site-packages\stable_baselines3\common\vec_env\patch_gym.py:49: UserWarning: You provided an OpenAI Gym environment. We strongly recommend transitioning to Gymnasium environments. Stable-Baselines3 is automatically wrapping your environments in a compatibility layer, which could potentially cause issues.
  warnings.warn(


3. Train the RL Model

In [1]:
%pip install torch torchvision torchaudio --index-url https://download.pytorch.org/whl/cu121


Looking in indexes: https://download.pytorch.org/whl/cu121
  Using cached https://download.pytorch.org/whl/cu121/torchvision-0.16.1%2Bcu121-cp38-cp38-win_amd64.whl (5.6 MB)
  Using cached https://download.pytorch.org/whl/cu121/torchaudio-2.1.1%2Bcu121-cp38-cp38-win_amd64.whl (4.0 MB)
Note: you may need to restart the kernel to use updated packages.


You should consider upgrading via the 'c:\Users\Gebruiker\AppData\Local\Programs\Python\Python38\python.exe -m pip install --upgrade pip' command.


In [5]:
# Import os for file path management
import os
#import PPO for aLgos
from stable_baselines3 import PPO
# Import Base Callback for saving models
from stable_baselines3.common.callbacks import BaseCallback
from nes_py.wrappers import JoypadSpace
JoypadSpace.reset = lambda self, **kwargs: self.env.reset(**kwargs)

In [6]:
# This code below is to be able to save the model overtime for if something goes wrong
# check_freq    = How often we want to save the model
# save_path     = Where we want to save the model to
class TrainAndLoggingCallback(BaseCallback):

    def __init__(self, check_freq, save_path, start_step, verbose=1):
        super(TrainAndLoggingCallback, self).__init__(verbose)
        self.check_freq = check_freq
        self.save_path = save_path
        self.start_step = start_step  # Add a start_step parameter

    def _init_callback(self):
        if self.save_path is not None:
            os.makedirs(self.save_path, exist_ok=True)

    def _on_step(self):
        if self.n_calls % self.check_freq == 0:
            model_step = self.n_calls + self.start_step  # Calculate the model's step
            model_path = os.path.join(self.save_path, 'best_model_{}'.format(model_step))
            self.model.save(model_path)

        return True


In [7]:
CHECKPOINT_DIR = './train/'
LOG_DIR = './logs/'

In [9]:
# Setup Model saving callback

# Calculate the last saved model's step number (e.g., 1000000)
last_saved_step = 2000000

# Setup Model saving callback with the last saved step as the start_step
callback = TrainAndLoggingCallback(check_freq=100000, save_path=CHECKPOINT_DIR, start_step=last_saved_step)


In [10]:
# This is the AI model started
# PPO is the algorithm we are using to train the model - https://stable-baselines3.readthedocs.io/en/master/modules/ppo.html
# CnnPolicy is the type of neural network that is really fast with images, we can also use MlpPolicy 
# n_steps - The number of steps for each environment per update
model = PPO('CnnPolicy', env, verbose=1, learning_rate=0.000001, n_steps=512, tensorboard_log=LOG_DIR)

Using cuda device
Wrapping the env in a VecTransposeImage.


In [10]:
# Train the AI model, this is where the AI model starts to learn
model.learn(total_timesteps=1000000, callback=callback)

Logging to ./logs/PPO_1


c:\Users\Gebruiker\AppData\Local\Programs\Python\Python38\lib\site-packages\gym\utils\passive_env_checker.py:233: DeprecationWarning: `np.bool8` is a deprecated alias for `np.bool_`.  (Deprecated NumPy 1.24)
  if not isinstance(terminated, (bool, np.bool8)):


----------------------------
| time/              |     |
|    fps             | 42  |
|    iterations      | 1   |
|    time_elapsed    | 12  |
|    total_timesteps | 512 |
----------------------------
-------------------------------------------
| time/                   |               |
|    fps                  | 8             |
|    iterations           | 2             |
|    time_elapsed         | 120           |
|    total_timesteps      | 1024          |
| train/                  |               |
|    approx_kl            | 3.4792465e-05 |
|    clip_fraction        | 0             |
|    clip_range           | 0.2           |
|    entropy_loss         | -1.95         |
|    explained_variance   | 0.00092       |
|    learning_rate        | 1e-06         |
|    loss                 | 197           |
|    n_updates            | 10            |
|    policy_gradient_loss | -0.000317     |
|    value_loss           | 488           |
-------------------------------------------
-----

In [11]:
# Training further
pretrained_model_path = './train/best_model_2000000'
pretrained_model = PPO.load(pretrained_model_path, env=env)

Wrapping the env in a VecTransposeImage.


In [12]:
pretrained_model.learn(total_timesteps=2000000, callback=callback)


Logging to ./logs/PPO_6


c:\Users\Gebruiker\AppData\Local\Programs\Python\Python38\lib\site-packages\gym\utils\passive_env_checker.py:233: DeprecationWarning: `np.bool8` is a deprecated alias for `np.bool_`.  (Deprecated NumPy 1.24)
  if not isinstance(terminated, (bool, np.bool8)):


----------------------------
| time/              |     |
|    fps             | 42  |
|    iterations      | 1   |
|    time_elapsed    | 11  |
|    total_timesteps | 512 |
----------------------------
------------------------------------------
| time/                   |              |
|    fps                  | 27           |
|    iterations           | 2            |
|    time_elapsed         | 36           |
|    total_timesteps      | 1024         |
| train/                  |              |
|    approx_kl            | 0.0111457165 |
|    clip_fraction        | 0.0248       |
|    clip_range           | 0.2          |
|    entropy_loss         | -1           |
|    explained_variance   | 0.896        |
|    learning_rate        | 1e-06        |
|    loss                 | 17.1         |
|    n_updates            | 39070        |
|    policy_gradient_loss | -0.00455     |
|    value_loss           | 51.2         |
------------------------------------------
-----------------------

4. Test it Out

In [45]:
# Load Model
model = PPO.load('./train/best_model_2000000')

In [46]:
# Start the game
state = env.reset()
# Loop trhough the game
while True:
    action, _ = model.predict(state)
    state, reward, done, info = env.step(action)
    env.render()

c:\Users\Gebruiker\AppData\Local\Programs\Python\Python38\lib\site-packages\gym\utils\passive_env_checker.py:233: DeprecationWarning: `np.bool8` is a deprecated alias for `np.bool_`.  (Deprecated NumPy 1.24)
  if not isinstance(terminated, (bool, np.bool8)):
c:\Users\Gebruiker\AppData\Local\Programs\Python\Python38\lib\site-packages\gym\utils\passive_env_checker.py:272: UserWarning: WARN: No render modes was declared in the environment (env.metadata['render_modes'] is None or not defined), you may have trouble when calling `.render()`.
  logger.warn(


KeyboardInterrupt: 